# Rental Market Analysis

This notebook analyzes the current rental market data from Bina.az.
**Dataset:** `data/rent/bina_rent_20251222_165530.csv`

In [32]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

print("Libraries imported.")

Libraries imported.


In [33]:
# Load Data
rent_data_path = 'data/rent/bina_rent_20251222_165530.csv'

print(f"Loading rent data from {rent_data_path}...")
try:
    df_rent = pd.read_csv(rent_data_path)
    print(f"Rent data loaded: {df_rent.shape}")
    display(df_rent.head(3))
except Exception as e:
    print(f"Error loading rent data: {e}")

Loading rent data from data/rent/bina_rent_20251222_165530.csv...
Rent data loaded: (28791, 30)


id  area_value area_units  leased  floor  floors  rooms  city_id  \
0  5751950       110.0         m²    True    9.0    17.0    3.0        1   
1  5757385        80.0         m²    True    NaN     NaN    3.0        1   
2  5523635        78.0         m²    True   12.0    18.0    2.0        1   

  city_name  location_id  ... paid_daily is_business  vipped featured  \
0      Bakı         33.0  ...      False        True   False    False   
1      Bakı         77.0  ...      False       False   False    False   
2      Bakı         36.0  ...      False        True   False    False   

                  updated_at            path photos_count  \
0  2025-12-22T16:35:18+04:00  /items/5751950           14   
1  2025-12-22T16:35:16+04:00  /items/5757385            6   
2  2025-12-22T16:34:23+04:00  /items/5523635           23   

                                              photos  \
0  [{"thumbnail": "https://bina.azstatic.com/uplo...   
1  [{"thumbnail": "https://bina.azstatic.com/uplo...   
2  [{"thumbnail": "https://bina.azstatic.com/uplo...   

                             url                  scraped_at  
0  https://bina.az/items/5751950  2025-12-22T16:35:20.661475  
1  https://bina.az/items/5757385  2025-12-22T16:35:20.661513  
2  https://bina.az/items/5523635  2025-12-22T16:35:20.661538  

[3 rows x 30 columns]

In [34]:
# Data Cleaning and Feature Engineering

def clean_rent_data(df):
    # Ensure price_value is numeric
    if 'price_value' in df.columns:
        df['price_value'] = pd.to_numeric(df['price_value'], errors='coerce')
    
    # Ensure area is numeric
    if 'area_value' in df.columns:
        df['area_value'] = pd.to_numeric(df['area_value'], errors='coerce')
    
    # Convert 'sot' to m^2 (1 sot = 100 m^2)
    if 'area_units' in df.columns and 'area_value' in df.columns:
        mask_sot = df['area_units'] == 'sot'
        df.loc[mask_sot, 'area_value'] = df.loc[mask_sot, 'area_value'] * 100
        df.loc[mask_sot, 'area_units'] = 'm²'
        
    # Calculate Rent per m^2
    if 'price_value' in df.columns and 'area_value' in df.columns:
        df['rent_per_m2'] = df['price_value'] / df['area_value']
        # Remove infinite or very large values which might be errors
        df.replace([np.inf, -np.inf], np.nan, inplace=True)
    
    # Convert boolean-like columns to proper boolean type
    boolean_columns = ['has_repair', 'has_bill_of_sale', 'has_mortgage', 'featured', 'is_business', 'paid_daily', 'vipped', 'leased']
    for col in boolean_columns:
        if col in df.columns:
            # Convert object type booleans (True/False strings or actual booleans) to proper boolean
            df[col] = df[col].map(lambda x: pd.isna(x) or (x is True or x == True or str(x).lower() == 'true'))
        
    return df

df_rent = clean_rent_data(df_rent)

print("Data cleaned.")
print(f"Valid rent prices: {df_rent['price_value'].notna().sum()}")
print(f"Valid rent/m2: {df_rent['rent_per_m2'].notna().sum()}")
print(f"\nBoolean Column Types:")
for col in ['has_repair', 'has_bill_of_sale', 'has_mortgage', 'featured', 'is_business', 'paid_daily']:
    if col in df_rent.columns:
        print(f"  {col}: {df_rent[col].dtype} - True count: {(df_rent[col] == True).sum()}")

Data cleaned.
Valid rent prices: 28791
Valid rent/m2: 28791

Boolean Column Types:
  has_repair: bool - True count: 28505
  has_bill_of_sale: bool - True count: 0
  has_mortgage: bool - True count: 0
  featured: bool - True count: 124
  is_business: bool - True count: 21560
  paid_daily: bool - True count: 1512


In [35]:
# Rent Price Distribution
price_limit = df_rent['price_value'].quantile(0.99)
data_to_plot = df_rent[df_rent['price_value'] < price_limit]['price_value'].dropna()

fig = px.histogram(data_to_plot, nbins=50,
                   title='Monthly Rent Price Distribution',
                   labels={'value': 'Rent Price (AZN)', 'count': 'Count'},
                   marginal='box')
fig.update_layout(showlegend=False, height=500)
fig.show()

# Rent per m2 Distribution
m2_limit = df_rent['rent_per_m2'].quantile(0.99)
data_m2_plot = df_rent[df_rent['rent_per_m2'] < m2_limit]['rent_per_m2'].dropna()

fig = px.histogram(data_m2_plot, nbins=50,
                   title='Rent per m² Distribution',
                   labels={'value': 'Rent per m² (AZN)', 'count': 'Count'},
                   marginal='box',
                   color_discrete_sequence=['orange'])
fig.update_layout(showlegend=False, height=500)
fig.show()

print("Rent Price Summary:")
print(df_rent['price_value'].describe().apply(lambda x: format(x, 'f')))

Rent Price Summary:
count     28791.000000
mean       1572.172728
std        5635.290736
min          10.000000
25%         650.000000
50%         950.000000
75%        1500.000000
max      750000.000000
Name: price_value, dtype: object


In [36]:
# Top Cities by Listing Count
if 'city_name' in df_rent.columns:
    top_cities = df_rent['city_name'].value_counts().head(10)
    
    fig = px.bar(x=top_cities.index, y=top_cities.values,
                 title='Top 10 Cities by Number of Rental Listings',
                 labels={'x': 'City', 'y': 'Number of Listings'},
                 color=top_cities.values,
                 color_continuous_scale='Viridis')
    fig.update_layout(showlegend=False, height=500)
    fig.show()
    
    # Average Rent by City (Top 10)
    avg_rent_city = df_rent.groupby('city_name')['price_value'].mean().loc[top_cities.index]
    
    fig = px.bar(x=avg_rent_city.index, y=avg_rent_city.values,
                 title='Average Monthly Rent in Top 10 Cities',
                 labels={'x': 'City', 'y': 'Average Rent (AZN)'},
                 color=avg_rent_city.values,
                 color_continuous_scale='Oranges')
    fig.update_layout(showlegend=False, height=500)
    fig.show()

In [37]:
# Room Count Analysis
if 'rooms' in df_rent.columns:
    # Clean room column if necessary
    df_rent['rooms'] = pd.to_numeric(df_rent['rooms'], errors='coerce')
    
    # Filter for reasonable room counts (e.g., 1 to 6 rooms)
    room_data = df_rent[(df_rent['rooms'] >= 1) & (df_rent['rooms'] <= 6)]
    
    # Remove outliers for price_value
    p1 = room_data['price_value'].quantile(0.01)
    p99 = room_data['price_value'].quantile(0.99)
    filtered_room_data = room_data[(room_data['price_value'] >= p1) & (room_data['price_value'] <= p99)]
    
    fig = px.box(filtered_room_data, x='rooms', y='price_value',
                 title='Monthly Rent Distribution by Room Count (Outliers Removed)',
                 labels={'rooms': 'Number of Rooms', 'price_value': 'Rent Price (AZN)'},
                 color='rooms',
                 color_discrete_sequence=px.colors.qualitative.Set3)
    fig.update_layout(height=500, showlegend=False)
    fig.show()
    
    # Remove outliers for rent_per_m2
    m2_p1 = room_data['rent_per_m2'].quantile(0.01)
    m2_p99 = room_data['rent_per_m2'].quantile(0.99)
    filtered_avg_by_room = room_data[(room_data['rent_per_m2'] >= m2_p1) & (room_data['rent_per_m2'] <= m2_p99)]
    avg_by_room_filtered = filtered_avg_by_room.groupby('rooms')['rent_per_m2'].mean().reset_index()
    
    fig = px.bar(avg_by_room_filtered, x='rooms', y='rent_per_m2',
                 title='Average Rent per m² by Room Count (Outliers Removed)',
                 labels={'rooms': 'Number of Rooms', 'rent_per_m2': 'Rent per m² (AZN)'},
                 color='rent_per_m2',
                 color_continuous_scale='YlOrRd')
    fig.update_layout(height=500, showlegend=False)
    fig.show()

In [38]:
# Deep Dive: Baku Regions (Rent)

def analyze_baku_rent_regions(df, top_n=20):
    print("\n--- Deep Dive: Baku (Bakı) Rental Market ---")
    
    baku_data = df[df['city_name'] == 'Bakı'].copy()
    
    if baku_data.empty:
        print("No data for Baku.")
        return

    # Group by location/region
    region_stats = baku_data.groupby('location_name').agg({
        'price_value': 'mean',
        'rent_per_m2': 'mean',
        'id': 'count'
    }).rename(columns={'id': 'listing_count', 'price_value': 'avg_rent', 'rent_per_m2': 'avg_rent_m2'})
    
    # Filter for regions with significant volume
    region_stats = region_stats[region_stats['listing_count'] > 10]
    
    # Sort by Rent per m2 (Most Expensive)
    top_expensive = region_stats.sort_values('avg_rent_m2', ascending=False).head(top_n)
    top_expensive_display = top_expensive.copy()
    top_expensive_display['Label'] = top_expensive_display.index + ' (Avg: ' + top_expensive_display['avg_rent'].round(0).astype(str) + ' AZN)'
    
    print(f"Top {top_n} Most Expensive Regions in Baku (by Rent/m²):")
    display(top_expensive)
    
    # Visualize Top Expensive
    fig = px.bar(top_expensive_display, 
                 y='Label', 
                 x='avg_rent_m2',
                 orientation='h',
                 title=f'Top {top_n} Most Expensive Regions in Baku (Rent per m² | Avg Price in AZN)',
                 labels={'avg_rent_m2': 'Rent per m² (AZN)', 'Label': 'Region (Avg Monthly Rent)'},
                 color='avg_rent_m2',
                 color_continuous_scale='Reds',
                 hover_data={'avg_rent': ':.0f', 'avg_rent_m2': ':.2f'})
    fig.update_layout(height=700, showlegend=False)
    fig.show()
    
    # Sort by Volume (Most Popular)
    top_volume = region_stats.sort_values('listing_count', ascending=False).head(top_n)
    
    fig = px.bar(top_volume, 
                 y=top_volume.index, 
                 x='listing_count',
                 orientation='h',
                 title=f'Top {top_n} Most Popular Rental Regions in Baku (by Volume)',
                 labels={'listing_count': 'Number of Listings', 'y': 'Region'},
                 color='listing_count',
                 color_continuous_scale='Blues')
    fig.update_layout(height=700, showlegend=False)
    fig.show()

analyze_baku_rent_regions(df_rent)


--- Deep Dive: Baku (Bakı) Rental Market ---
Top 20 Most Expensive Regions in Baku (by Rent/m²):


avg_rent  avg_rent_m2  listing_count
location_name                                              
Abşeron             2715.625000   100.035995             24
Ağ şəhər            3299.864407    21.451573           1239
Sahil               2010.152985    18.086527            804
NZS                 1165.714286    17.705862             21
28 May              2118.528275    16.841004           2122
İçəri Şəhər         2304.966074    16.471536            619
Xətai               2093.527311    15.541683            476
Elmlər Akademiyası  1748.864530    15.060861           1373
Səbail              2063.914980    14.889199            247
Sea Breeze          1339.148148    14.744911            108
Şıxov               5259.722222    14.257474             18
Nizami              1577.746556    14.087977           1452
Bayıl               1653.458564    14.006560            181
Şah İsmayıl Xətai   1619.236297    13.688528           2171
Böyükşor            2866.666667    13.611946             12
Kubinka             1631.727273    13.466912             11
Gənclik             1468.657603    13.236228            993
Nəsimi              1679.931677    13.090414           1610
Nəriman Nərimanov   1366.157770    12.811229           2117
Bakmil              1394.900000    12.775069             70

In [39]:
# Deep Dive: Room Count Analysis by Region (Rent)

def analyze_baku_rent_regions_rooms(df, top_n=20, min_listings=5):
    print("\n--- Deep Dive: Baku (Bakı) Rental Market by Room Count ---")
    
    baku_data = df[df['city_name'] == 'Bakı'].copy()
    
    if baku_data.empty:
        print("No data for Baku.")
        return

    # Ensure rooms is numeric
    baku_data['rooms'] = pd.to_numeric(baku_data['rooms'], errors='coerce')

    # Group by location/region and rooms
    region_room_stats = baku_data.groupby(['location_name', 'rooms']).agg({
        'price_value': 'mean',
        'rent_per_m2': 'mean',
        'id': 'count'
    }).rename(columns={'id': 'listing_count', 'price_value': 'avg_rent', 'rent_per_m2': 'avg_rent_m2'})
    
    # Filter for significant volume
    region_room_stats = region_room_stats[region_room_stats['listing_count'] >= min_listings]
    
    # Reset index for easier plotting
    region_room_stats = region_room_stats.reset_index()
    
    # Sort by Rent per m2 (Most Expensive)
    top_expensive = region_room_stats.sort_values('avg_rent_m2', ascending=False).head(top_n)
    
    print(f"Top {top_n} Most Expensive Region-Room Combinations in Baku (by Rent/m²):")
    display(top_expensive)
    
    # Visualize Top Expensive with Avg Price
    if not top_expensive.empty:
        top_expensive_display = top_expensive.copy()
        top_expensive_display['Label'] = top_expensive_display['location_name'] + ' (' + top_expensive_display['rooms'].astype(int).astype(str) + ' rooms | Avg: ' + top_expensive_display['avg_rent'].round(0).astype(str) + ' AZN)'
        
        fig = px.bar(top_expensive_display, 
                     y='Label', 
                     x='avg_rent_m2',
                     orientation='h',
                     title=f'Top {top_n} Most Expensive Region-Room Combinations in Baku (Rent per m² | Avg Price)',
                     labels={'avg_rent_m2': 'Rent per m² (AZN)', 'Label': 'Region (Rooms | Avg Monthly Rent)'},
                     color='avg_rent_m2',
                     hover_data={'avg_rent': ':.0f', 'avg_rent_m2': ':.2f'},
                     color_continuous_scale='Plasma')
        fig.update_layout(height=700, showlegend=False)
        fig.show()

analyze_baku_rent_regions_rooms(df_rent)


--- Deep Dive: Baku (Bakı) Rental Market by Room Count ---
Top 20 Most Expensive Region-Room Combinations in Baku (by Rent/m²):


location_name  rooms      avg_rent  avg_rent_m2  listing_count
81   Elmlər Akademiyası   15.0  16200.000000    40.500000              5
9                28 May    4.0   5265.330357    27.408167            224
36             Ağ şəhər    1.0   1157.692308    24.590607             26
173               Sahil    1.0    732.750000    23.586095             64
233   Şah İsmayıl Xətai   20.0  22977.777778    22.515152              9
37             Ağ şəhər    2.0   1640.269802    22.228537            404
39             Ağ şəhər    4.0   3386.619565    21.041214             92
82              Günəşli    2.0   1021.666667    20.813967              6
188              Səbail    5.0   5400.000000    20.147746              5
40             Ağ şəhər    5.0   4371.153846    20.059250             26
12               28 May   20.0  17916.666667    19.916207              6
194               Xətai    1.0   1242.111111    19.781783              9
38             Ağ şəhər    3.0   2307.504348    18.986713            575
6                28 May    1.0    626.606838    18.779480            117
145   Nəriman Nərimanov    7.0   4893.208333    18.538774             24
83              Gənclik    1.0    988.666667    18.504715             48
198               Xətai    5.0   3690.000000    18.225518              5
128              Nizami    1.0    607.810127    17.808187             79
139   Nəriman Nərimanov    1.0    585.612069    17.446820            116
229   Şah İsmayıl Xətai    5.0   3229.259259    17.436875             27

## 📊 Interactive Dashboard: Rental Market by Room Size
Comprehensive analysis of rental market segmented by room count.

In [40]:
# Comprehensive Room Size Dashboard for Rentals

# Prepare data
df_rent['rooms'] = pd.to_numeric(df_rent['rooms'], errors='coerce')
room_data = df_rent[(df_rent['rooms'] >= 1) & (df_rent['rooms'] <= 6)].copy()

# Create comprehensive dashboard
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Room Distribution in Rentals', 'Rent Price by Room Count',
                    'Rent per m² by Room Count', 'Listing Count by City & Rooms'),
    specs=[[{'type': 'bar'}, {'type': 'box'}],
           [{'type': 'bar'}, {'type': 'bar'}]]
)

# 1. Room distribution
room_counts = room_data['rooms'].value_counts().sort_index()
fig.add_trace(go.Bar(x=room_counts.index, y=room_counts.values, 
                     name='Listings', marker_color='teal'),
              row=1, col=1)

# 2. Box plot for rent by rooms
for room in sorted(room_data['rooms'].dropna().unique()):
    room_prices = room_data[room_data['rooms'] == room]['price_value']
    # Filter outliers for better visualization
    q99 = room_prices.quantile(0.99)
    room_prices_filtered = room_prices[room_prices < q99]
    fig.add_trace(go.Box(y=room_prices_filtered,
                        name=f'{int(room)} room', showlegend=False),
                 row=1, col=2)

# 3. Average rent per m2 by room count
avg_rent_m2_by_room = room_data.groupby('rooms')['rent_per_m2'].mean()
fig.add_trace(go.Bar(x=avg_rent_m2_by_room.index, y=avg_rent_m2_by_room.values,
                    marker_color='coral', showlegend=False),
             row=2, col=1)

# 4. Stacked bar for top cities by rooms
top_cities = room_data['city_name'].value_counts().head(5).index
for room in [1, 2, 3, 4]:
    city_room_counts = []
    for city in top_cities:
        count = len(room_data[(room_data['city_name'] == city) & (room_data['rooms'] == room)])
        city_room_counts.append(count)
    fig.add_trace(go.Bar(name=f'{room} rooms', x=top_cities, y=city_room_counts),
                 row=2, col=2)

# Update layout
fig.update_xaxes(title_text="Number of Rooms", row=1, col=1)
fig.update_xaxes(title_text="Number of Rooms", row=1, col=2)
fig.update_xaxes(title_text="Number of Rooms", row=2, col=1)
fig.update_xaxes(title_text="City", row=2, col=2)

fig.update_yaxes(title_text="Count", row=1, col=1)
fig.update_yaxes(title_text="Rent Price (AZN)", row=1, col=2)
fig.update_yaxes(title_text="Rent per m² (AZN)", row=2, col=1)
fig.update_yaxes(title_text="Listing Count", row=2, col=2)

fig.update_layout(height=800, title_text="Rental Market Room Size Dashboard", 
                  barmode='stack', showlegend=True)
fig.show()

In [41]:
# Room Size Analysis Heatmap by Top Cities

# Get top 5 cities
top_5_cities = df_rent['city_name'].value_counts().head(5).index

# Prepare data
room_city_rent_data = []
for city in top_5_cities:
    city_data = df_rent[(df_rent['city_name'] == city) & 
                        (df_rent['rooms'].between(1, 6))].copy()
    
    for room in range(1, 7):
        avg_rent = city_data[city_data['rooms'] == room]['price_value'].mean()
        avg_rent_m2 = city_data[city_data['rooms'] == room]['rent_per_m2'].mean()
        count = len(city_data[city_data['rooms'] == room])
        
        if pd.notna(avg_rent) and count >= 5:
            room_city_rent_data.append({
                'City': city,
                'Rooms': room,
                'Avg Rent': avg_rent,
                'Avg Rent/m²': avg_rent_m2,
                'Count': count
            })

df_room_city_rent = pd.DataFrame(room_city_rent_data)

# Create heatmaps
if not df_room_city_rent.empty:
    # Heatmap 1: Average Rent
    pivot_rent = df_room_city_rent.pivot(index='City', columns='Rooms', values='Avg Rent')
    
    fig = go.Figure(data=go.Heatmap(
        z=pivot_rent.values,
        x=[f'{int(col)} rooms' for col in pivot_rent.columns],
        y=pivot_rent.index,
        colorscale='YlOrRd',
        text=pivot_rent.values.round(0),
        texttemplate='%{text} AZN',
        textfont={"size": 11},
        colorbar=dict(title="Avg Rent (AZN)")
    ))
    
    fig.update_layout(
        title='Average Monthly Rent Heatmap: Top Cities by Room Count',
        xaxis_title='Number of Rooms',
        yaxis_title='City',
        height=500
    )
    fig.show()
    
    # Heatmap 2: Rent per m² with Avg Price
    pivot_rent_m2 = df_room_city_rent.pivot(index='City', columns='Rooms', values='Avg Rent/m²')
    pivot_avg_rent = df_room_city_rent.pivot(index='City', columns='Rooms', values='Avg Rent')
    
    # Create custom hover text combining both metrics
    hover_text = []
    for i, city in enumerate(pivot_rent_m2.index):
        city_hover = []
        for j, col in enumerate(pivot_rent_m2.columns):
            rent_m2 = pivot_rent_m2.iloc[i, j]
            avg_rent = pivot_avg_rent.iloc[i, j]
            if pd.notna(rent_m2) and pd.notna(avg_rent):
                city_hover.append(f'{rent_m2:.2f}<br>Avg: {avg_rent:.0f} AZN')
            else:
                city_hover.append('')
        hover_text.append(city_hover)
    
    fig = go.Figure(data=go.Heatmap(
        z=pivot_rent_m2.values,
        x=[f'{int(col)} rooms' for col in pivot_rent_m2.columns],
        y=pivot_rent_m2.index,
        colorscale='Viridis',
        text=hover_text,
        texttemplate='%{text}',
        textfont={"size": 10},
        hovertemplate='<b>%{y} - %{x}</b><br>%{text}<extra></extra>',
        colorbar=dict(title="Rent/m² (AZN)")
    ))
    
    fig.update_layout(
        title='Rent per m² Heatmap with Avg Monthly Rent: Top Cities by Room Count',
        xaxis_title='Number of Rooms',
        yaxis_title='City',
        height=500
    )
    fig.show()

In [42]:
# Interactive Scatter: Area vs Rent by Room Count

# Filter for reasonable values
scatter_rent_data = df_rent[
    (df_rent['area_value'].between(20, 300)) &
    (df_rent['price_value'].between(200, 10000)) &
    (df_rent['rooms'].between(1, 6))
].copy()

scatter_rent_data['rooms_str'] = scatter_rent_data['rooms'].astype(int).astype(str) + ' rooms'

fig = px.scatter(scatter_rent_data, 
                 x='area_value', 
                 y='price_value',
                 color='rooms_str',
                 size='rent_per_m2',
                 hover_data=['city_name', 'location_name', 'rent_per_m2'],
                 title='Rental Property: Area vs Monthly Rent (colored by Room Count)',
                 labels={'area_value': 'Area (m²)', 
                        'price_value': 'Monthly Rent (AZN)',
                        'rooms_str': 'Rooms'},
                 opacity=0.6,
                 color_discrete_sequence=px.colors.qualitative.Pastel)

fig.update_layout(height=600)
fig.show()

In [43]:
# Detailed Room Analysis for Baku Regions

baku_room_data = df_rent[(df_rent['city_name'] == 'Bakı') & 
                         (df_rent['rooms'].between(1, 4))].copy()

# Get top 10 regions by volume
top_regions = baku_room_data['location_name'].value_counts().head(10).index

# Prepare data for grouped bar chart
region_room_comparison = []
for region in top_regions:
    for room in [1, 2, 3, 4]:
        region_room_subset = baku_room_data[
            (baku_room_data['location_name'] == region) & 
            (baku_room_data['rooms'] == room)
        ]
        if len(region_room_subset) >= 3:
            avg_rent = region_room_subset['price_value'].mean()
            region_room_comparison.append({
                'Region': region,
                'Rooms': f'{room} rooms',
                'Avg Rent': avg_rent
            })

df_region_room_comp = pd.DataFrame(region_room_comparison)

if not df_region_room_comp.empty:
    fig = px.bar(df_region_room_comp, 
                 x='Region', 
                 y='Avg Rent',
                 color='Rooms',
                 barmode='group',
                 title='Average Monthly Rent by Region and Room Count (Baku)',
                 labels={'Avg Rent': 'Average Monthly Rent (AZN)'},
                 color_discrete_sequence=px.colors.qualitative.Set2,
                 height=600)
    fig.update_layout(xaxis_tickangle=-45)
    fig.show()

In [44]:
# Create regional summary dataframe for visualization
baku_data = df_rent[df_rent['city_name'] == 'Bakı'].copy()

# Group by region and calculate metrics
df_rent_regions = baku_data.groupby('location_name').agg({
    'price_value': 'mean',
    'rent_per_m2': 'mean',
    'area_value': 'mean',
    'id': 'count'
}).reset_index()

df_rent_regions.columns = ['Region', 'Avg Monthly Rent', 'Avg Rent/m²', 'Avg Area (m²)', 'Listing Count']

# Filter for regions with at least 10 listings
df_rent_regions = df_rent_regions[df_rent_regions['Listing Count'] >= 10].sort_values('Avg Rent/m²', ascending=False)

print(f"Regional Summary - {len(df_rent_regions)} regions with 10+ listings")
display(df_rent_regions.head(15))

Regional Summary - 77 regions with 10+ listings


Region  Avg Monthly Rent  Avg Rent/m²  Avg Area (m²)  \
12              Abşeron       2715.625000   100.035995     215.833333   
16             Ağ şəhər       3299.864407    21.451573     139.500323   
78                Sahil       2010.152985    18.086527     120.263060   
60                  NZS       1165.714286    17.705862     124.571429   
3                28 May       2118.528275    16.841004     120.694628   
99          İçəri Şəhər       2304.966074    16.471536     149.685137   
88                Xətai       2093.527311    15.541683     168.767227   
34   Elmlər Akademiyası       1748.864530    15.060861     119.351566   
83               Səbail       2063.914980    14.889199     143.655870   
80           Sea Breeze       1339.148148    14.744911     107.250000   
103               Şıxov       5259.722222    14.257474     442.388889   
63               Nizami       1577.746556    14.087977     116.603857   
22                Bayıl       1653.458564    14.006560     118.584530   
100   Şah İsmayıl Xətai       1619.236297    13.688528     116.111414   
28             Böyükşor       2866.666667    13.611946     305.833333   

     Listing Count  
12              24  
16            1239  
78             804  
60              21  
3             2122  
99             619  
88             476  
34            1373  
83             247  
80             108  
103             18  
63            1452  
22             181  
100           2171  
28              12

In [45]:
# Visualization 1: Rent per m² and Average Area (dual axis comparison)
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Bar(x=df_rent_regions['Region'], y=df_rent_regions['Avg Rent/m²'],
           name='Avg Rent/m²',
           customdata=df_rent_regions['Avg Monthly Rent'].round(0),
           hovertemplate='<b>%{x}</b><br>Rent/m²: %{y:.2f} AZN<br>Avg Price: %{customdata:.0f} AZN<extra></extra>',
           marker_color='salmon'),
    secondary_y=False
)

fig.add_trace(
    go.Scatter(x=df_rent_regions['Region'], y=df_rent_regions['Avg Area (m²)'],
              name='Avg Area', line=dict(color='darkblue', width=3), mode='lines+markers'),
    secondary_y=True
)

fig.update_layout(
    title='Baku Rental: Rent per m² (with Avg Price) vs Average Property Area by Region',
    xaxis_title='Region',
    height=600,
    xaxis_tickangle=-45,
    hovermode='x unified'
)
fig.update_yaxes(title_text='Rent per m² (AZN)', secondary_y=False)
fig.update_yaxes(title_text='Area (m²)', secondary_y=True)
fig.show()

In [48]:
# Visualization 1: Price Segments by Region (Top and Bottom)
# Categorize regions into segments based on Rent/m²
df_rent_regions['Rental Segment'] = pd.cut(df_rent_regions['Avg Rent/m²'], 
                                            bins=3, 
                                            labels=['Budget', 'Standard', 'Premium'])

segment_data = df_rent_regions.groupby('Rental Segment').agg({
    'Avg Rent/m²': 'mean',
    'Avg Monthly Rent': 'mean',
    'Listing Count': 'sum',
    'Avg Area (m²)': 'mean'
}).reset_index()

colors_rental = {'Premium': '#E74C3C', 'Standard': '#F39C12', 'Budget': '#27AE60'}
segment_colors = [colors_rental.get(seg, '#666') for seg in segment_data['Rental Segment']]

fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Avg Rent/m² by Segment', 'Market Share by Listings'),
    specs=[[{'type': 'bar'}, {'type': 'pie'}]]
)

fig.add_trace(
    go.Bar(x=segment_data['Rental Segment'].astype(str), y=segment_data['Avg Rent/m²'],
           customdata=segment_data['Avg Monthly Rent'].round(0),
           hovertemplate='<b>%{x}</b><br>Rent/m²: %{y:.2f} AZN<br>Avg Price: %{customdata:.0f} AZN<extra></extra>',
           marker_color=segment_colors, showlegend=False),
    row=1, col=1
)

fig.add_trace(
    go.Pie(labels=segment_data['Rental Segment'].astype(str), values=segment_data['Listing Count'],
           marker_colors=segment_colors),
    row=1, col=2
)

fig.update_yaxes(title_text='Rent/m² (AZN)', row=1, col=1)
fig.update_layout(height=500, title_text='Baku Rental: Market Segments Analysis', showlegend=False)
fig.show()

# Visualization 2: Value Analysis - Top 15 Regions
top_regions = df_rent_regions.head(15).copy()
top_regions['Value Score'] = (top_regions['Listing Count'] / top_regions['Listing Count'].max()) * 100 - \
                              (top_regions['Avg Rent/m²'] / top_regions['Avg Rent/m²'].max()) * 30

fig = px.scatter(top_regions,
                x='Listing Count',
                y='Avg Rent/m²',
                size='Avg Monthly Rent',
                color='Value Score',
                hover_name='Region',
                hover_data={'Avg Rent/m²': ':.2f', 'Avg Monthly Rent': ':.0f', 'Listing Count': True, 'Avg Area (m²)': ':.1f'},
                title='Baku Rental: Value Proposition Analysis (Top Expensive Regions)',
                labels={'Listing Count': 'Number of Active Listings',
                       'Avg Rent/m²': 'Rental Yield per m² (AZN)',
                       'Avg Monthly Rent': 'Avg Monthly Rent (AZN)'},
                color_continuous_scale='RdYlGn_r',
                height=600)

fig.update_layout(showlegend=True)
fig.show()

# Visualization 3: Regional Comparison - Area vs Rent Distribution
fig = px.scatter(df_rent_regions,
                x='Avg Area (m²)',
                y='Avg Rent/m²',
                size='Listing Count',
                color='Avg Monthly Rent',
                hover_name='Region',
                hover_data={'Avg Rent/m²': ':.2f', 'Avg Monthly Rent': ':.0f', 'Listing Count': True, 'Avg Area (m²)': ':.1f'},
                title='Baku Rental: Property Area vs Rent per m² (bubble size = listing count)',
                labels={'Avg Area (m²)': 'Average Property Area (m²)',
                       'Avg Rent/m²': 'Rent per m² (AZN)',
                       'Listing Count': 'Number of Listings'},
                color_continuous_scale='Viridis',
                height=600)

fig.update_layout(showlegend=True)
fig.show()

C:\Users\stmehdiyev\AppData\Local\Temp\ipykernel_13416\3225493045.py:7: FutureWarning:

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.



In [ ]:
# Rental Market Summary & Key Insights

rental_summary = {
    "Total Regions Analyzed": len(df_rent_regions),
    "Total Active Listings": df_rent_regions["Listing Count"].sum(),
    "Average Monthly Rent": df_rent_regions["Avg Monthly Rent"].mean(),
    "Average Rent/m²": df_rent_regions["Avg Rent/m²"].mean(),
    "Average Property Area": df_rent_regions["Avg Area (m²)"].mean(),
    "Most Active Region": df_rent_regions.loc[
        df_rent_regions["Listing Count"].idxmax(), "Region"
    ],
    "Most Expensive Region": df_rent_regions.loc[
        df_rent_regions["Avg Rent/m²"].idxmax(), "Region"
    ],
    "Most Affordable Region": df_rent_regions.loc[
        df_rent_regions["Avg Rent/m²"].idxmin(), "Region"
    ],
}

print("\n" + "=" * 130)
print("BAKU RENTAL MARKET: KEY SUMMARY METRICS")
print("=" * 130)
for key, value in rental_summary.items():
    if isinstance(value, float):
        if "Listings" in key and value > 100:
            print(f"{key:.<70} {value:>30,.0f}")
        else:
            print(f"{key:.<70} {value:>30,.2f}")
    else:
        print(f"{key:.<70} {value:>30}")

print("\n" + "=" * 130)
print("RENTAL SEGMENT BREAKDOWN")
print("=" * 130)

for segment in ["Premium", "Standard", "Budget"]:
    segment_data = df_rent_regions[df_rent_regions["Rental Segment"] == segment]
    if not segment_data.empty:
        print(f"\n{segment.upper()} SEGMENT:")
        print(f"  • Regions: {len(segment_data)}")
        print(f"  • Total Listings: {segment_data['Listing Count'].sum():,.0f}")
        print(f"  • Avg Rent/m²: {segment_data['Avg Rent/m²'].mean():,.2f} AZN")
        print(
            f"  • Avg Monthly Rent: {segment_data['Avg Monthly Rent'].mean():,.0f} AZN"
        )
        print(f"  • Avg Property Size: {segment_data['Avg Area (m²)'].mean():.1f} m²")

print("\n" + "=" * 130)
print("RENTAL MARKET CHARACTERISTICS")
print("=" * 130)
print(f"Overall Market Statistics:")
print(
    f"  • Total Market Volume: {df_rent['city_name'].value_counts().sum():,.0f} listings"
)
print(
    f"  • Baku Rental Listings (10+ regions): {df_rent_regions['Listing Count'].sum():,.0f} listings"
)
print(
    f"  • Price Range: {df_rent_regions['Avg Monthly Rent'].min():.0f} - {df_rent_regions['Avg Monthly Rent'].max():.0f} AZN/month"
)
print(
    f"  • Rent/m² Range: {df_rent_regions['Avg Rent/m²'].min():.2f} - {df_rent_regions['Avg Rent/m²'].max():.2f} AZN/m²/month"
)
print(
    f"  • Average Property Size: {df_rent_regions['Avg Area (m²)'].mean():.1f} m²"
)


BAKU RENTAL MARKET: KEY SUMMARY METRICS
Total Regions Analyzed................................................                             77
Total Active Listings.................................................                          27484
Average Monthly Rent..................................................                       1,835.69
Average Rent/m².......................................................                          10.74
Average Property Area.................................................                         352.75
Most Active Region....................................................              Şah İsmayıl Xətai
Most Expensive Region.................................................                        Abşeron
Most Affordable Region................................................                         Türkan

RENTAL SEGMENT BREAKDOWN

PREMIUM SEGMENT:
  • Regions: 1
  • Total Listings: 24
  • Avg Rent/m²: 100.04 AZN
  • Avg Monthly Rent: 2,716 AZN
 

: 

## 📊 Executive Summary: Baku Rental Market Insights

**Market Overview:**
- **Active Listings**: Comprehensive analysis of 15+ regions
- **Market Segments**: Premium, Standard, and Budget rental markets
- **Investment Potential**: Value analysis based on listing volume and rental yield
- **Quality Metrics**: Amenities, visibility, and service availability


# 🔍 Advanced Baku Rental Market Analysis
Deep analysis of Baku's rental market with multiple dimensions and field utilization.
